# Interactive Plotting with Plotly

Xarray provides interactive plotting capabilities using [Plotly Express](https://plotly.com/python/plotly-express/) through the `.plotly` accessor on DataArrays. This enables creating interactive, zoomable, and hoverable plots directly from xarray data structures.

This notebook demonstrates the full range of plotting options using the NCEP/NCAR Reanalysis air temperature dataset.

## Setup and Data

In [1]:
import numpy as np
import xarray as xr

In [2]:
# Load tutorial data: 2 years of 6-hourly air temperature
airtemps: xr.Dataset = xr.tutorial.open_dataset("air_temperature")

# Convert to Celsius and preserve attributes
air = airtemps.air - 273.15
air.attrs = airtemps.air.attrs
air.attrs["units"] = "deg C"
air.attrs["long_name"] = "Air Temperature"

print(f"Dataset shape: {air.shape}")
print(f"Dimensions: {air.dims}")
print(f"Time range: {air.time.values[0]} to {air.time.values[-1]}")
air

Dataset shape: (2920, 25, 53)
Dimensions: ('time', 'lat', 'lon')
Time range: 2013-01-01T00:00:00.000000000 to 2014-12-31T18:00:00.000000000


<xarray.DataArray 'air' (time: 2920, lat: 25, lon: 53)> Size: 31MB
array([[[-31.95, -30.65, -29.65, ..., -40.35, -37.65, -34.55],
        [-29.35, -28.65, -28.45, ..., -40.35, -37.85, -33.85],
        [-23.15, -23.35, -24.26, ..., -39.95, -36.76, -31.45],
        ...,
        [ 23.45,  23.05,  23.25, ...,  22.25,  21.95,  21.55],
        [ 22.75,  23.05,  23.64, ...,  22.75,  22.75,  22.05],
        [ 23.14,  23.64,  23.95, ...,  23.75,  23.64,  23.45]],

       [[-31.05, -30.45, -30.05, ..., -41.15, -39.55, -37.35],
        [-29.55, -29.05, -28.95, ..., -42.15, -40.65, -37.45],
        [-19.95, -20.26, -21.05, ..., -42.35, -39.76, -34.65],
        ...,
        [ 23.25,  22.75,  23.05, ...,  22.25,  21.95,  21.64],
        [ 23.05,  23.55,  23.64, ...,  22.45,  22.35,  21.95],
        [ 23.14,  24.05,  24.25, ...,  23.25,  23.25,  23.45]],

       [[-30.85, -30.95, -30.85, ..., -38.85, -37.05, -34.45],
        [-28.55, -28.76, -29.15, ..., -42.85, -41.15, -37.45],
        [-16.95, -17.65, -18.95, ..., -41.95, -39.95, -34.95],
        ...,
...
        [ 21.64,  22.14,  24.34, ...,  22.34,  22.24,  21.54],
        [ 23.64,  24.74,  25.14, ...,  22.34,  22.34,  21.64],
        [ 25.04,  26.04,  25.64, ...,  22.94,  22.64,  22.64]],

       [[-27.36, -28.36, -29.66, ..., -29.86, -29.16, -28.36],
        [-23.26, -23.86, -24.66, ..., -31.86, -30.66, -28.86],
        [-10.76, -11.36, -11.86, ..., -32.66, -30.06, -26.26],
        ...,
        [ 20.54,  20.74,  22.24, ...,  21.94,  21.54,  21.14],
        [ 23.14,  24.04,  24.44, ...,  22.14,  21.94,  21.24],
        [ 24.64,  25.24,  25.34, ...,  22.54,  22.34,  22.04]],

       [[-28.06, -28.86, -29.86, ..., -31.46, -31.66, -31.36],
        [-23.26, -23.86, -24.76, ..., -33.56, -32.86, -31.46],
        [-10.16, -10.96, -11.76, ..., -33.26, -30.56, -26.86],
        ...,
        [ 20.64,  20.54,  21.94, ...,  22.14,  21.94,  21.54],
        [ 22.94,  23.74,  24.04, ...,  22.54,  22.54,  22.04],
        [ 24.54,  24.94,  24.94, ...,  23.34,  23.04,  22.54]]],
      shape=(2920, 25, 53))
Coordinates:
  * time     (time) datetime64[ns] 23kB 2013-01-01 ... 2014-12-31T18:00:00
  * lat      (lat) float32 100B 75.0 72.5 70.0 67.5 65.0 ... 22.5 20.0 17.5 15.0
  * lon      (lon) float32 212B 200.0 202.5 205.0 207.5 ... 325.0 327.5 330.0
Attributes:
    long_name:     Air Temperature
    units:         deg C
    precision:     2
    GRIB_id:       11
    GRIB_name:     TMP
    var_desc:      Air temperature
    dataset:       NMC Reanalysis
    level_desc:    Surface
    statistic:     Individual Obs
    parent_stat:   Other
    actual_range:  [185.16 322.1 ]

---
## Line Plots

Line plots show DataArray values on the y-axis. Dimensions fill slots in order:

**Slot order:** `x -> color -> line_dash -> symbol -> facet_col -> facet_row -> animation_frame`

### 1D: Simple Time Series

In [3]:
# Single location time series
nyc = air.sel(lat=40, lon=360-74, method="nearest")
nyc.plotly.line(title="New York City Temperature")

### 2D: Multiple Lines with Color

In [4]:
# Compare 3 latitudes at one longitude
# Automatic: time -> x, lat -> color
three_lats = air.sel(lon=250, lat=[60, 45, 30])
three_lats.plotly.line(title="Temperature by Latitude")

In [5]:
# Same data, but swap assignments: lat -> x, time -> color
# (subset time for clarity)
three_lats.isel(time=slice(0, 100, 10)).plotly.line(
    x="lat", color="time",
    title="Temperature Profile at Different Times"
)

### 3D: Using line_dash for a Third Dimension

In [6]:
# Monthly mean for multiple locations
monthly = air.sel(lat=[60, 30], lon=[220, 280]).resample(time="ME").mean()

# Automatic: time -> x, lat -> color, lon -> line_dash
monthly.plotly.line(title="Monthly Temperature: 2 Latitudes x 2 Longitudes")

In [7]:
# Skip color to use line_dash more prominently
monthly.plotly.line(
    x="time", color=None, line_dash="lat", symbol="lon",
    title="Using line_dash and symbol instead of color"
)

### Faceted Line Plots

In [8]:
# Use facet_col for separate panels
monthly.plotly.line(
    x="time", color="lat", facet_col="lon",
    title="Faceted by Longitude"
)

In [9]:
# Grid of facets: facet_row x facet_col
monthly.plotly.line(
    x="time", color=None, facet_col="lon", facet_row="lat",
    title="Grid Layout: Latitude x Longitude",
    height=500
)

---
## Bar Charts

**Slot order:** `x -> color -> pattern_shape -> facet_col -> facet_row -> animation_frame`

In [10]:
# Seasonal means for one location
seasonal = air.sel(lon=250, lat=45).groupby("time.season").mean()
seasonal.plotly.bar(title="Seasonal Temperature")

In [11]:
# Grouped bars: season x latitude
seasonal_lats = air.sel(lon=250, lat=[60, 45, 30]).groupby("time.season").mean()

# Automatic: season -> x, lat -> color
seasonal_lats.plotly.bar(title="Seasonal Temperature by Latitude")

In [12]:
# Swap: lat on x-axis, season as color
seasonal_lats.plotly.bar(
    x="lat", color="season",
    title="Temperature by Latitude (colored by Season)"
)

In [13]:
# Using pattern_shape for a third dimension (convert numeric dims to str for proper categorical coloring
seasonal_grid: xr.DataArray = air.sel(lat=[60, 30], lon=[220, 280]).groupby("time.season").mean()
seasonal_grid = seasonal_grid.assign_coords(lon=seasonal_grid.lon.astype(str))
seasonal_grid = seasonal_grid.assign_coords(lat=seasonal_grid.lat.astype(str))

seasonal_grid.plotly.bar(
    x="season", color="lat", pattern_shape="lon",
    title="Using pattern_shape for Longitude",
    barmode="group"
)

---
## Area Charts

**Slot order:** `x -> color -> pattern_shape -> facet_col -> facet_row -> animation_frame`

In [14]:
# Stacked area by latitude
monthly_lats = air.sel(lon=250, lat=[60, 45, 30]).resample(time="ME").mean()
# Shift values to be positive for meaningful stacking
monthly_positive = monthly_lats - monthly_lats.min() + 1

monthly_positive.plotly.area(title="Stacked Area by Latitude")

In [15]:
# Faceted area charts
monthly_grid = air.sel(lat=[60, 30], lon=[220, 280]).resample(time="ME").mean()
monthly_grid_pos = monthly_grid - monthly_grid.min() + 1

monthly_grid_pos.plotly.area(
    x="time", color="lat", facet_col="lon",
    title="Area Charts Faceted by Longitude"
)

---
## Scatter Plots

Scatter plots support two modes:
1. **Default:** y-axis shows DataArray values
2. **Dimension vs Dimension:** set `y` to a dimension name, use `color="value"` for temperature

**Slot order:** `x -> color -> size -> symbol -> facet_col -> facet_row -> animation_frame`

### Values on Y-Axis (default)

In [16]:
# Time series as scatter
sample = air.sel(lon=250, lat=45).isel(time=slice(0, 200))
sample.plotly.scatter(title="Temperature Scatter")

In [17]:
# Multiple latitudes with different symbols
sample_lats = air.sel(lon=250, lat=[60, 45, 30]).isel(time=slice(0, 100))

# Automatic: time -> x, lat -> color
sample_lats.plotly.scatter(title="Scatter by Latitude")

In [18]:
# Use symbol instead of color
sample_lats.plotly.scatter(
    x="time", color=None, symbol="lat",
    title="Using Symbol for Latitude"
)

### Dimension vs Dimension (Geographic Plot)

In [19]:
# Plot lat vs lon, colored by temperature
snapshot = air.isel(time=0)

snapshot.plotly.scatter(
    x="lon", y="lat", color="value",
    title="Spatial Temperature Distribution",
    color_continuous_scale="RdBu_r"
)

In [20]:
# Animated geographic scatter
daily = air.resample(time="D").mean().isel(time=slice(0, 30))

daily.plotly.scatter(
    x="lon", y="lat", color="value", animation_frame="time",
    title="Daily Temperature Animation",
    color_continuous_scale="RdBu_r",
    range_color=[-40, 30]
)

---
## Box Plots

Box plots aggregate unassigned dimensions into box statistics. By default, only `x` is auto-assigned; other slots default to `None` for aggregation.

**Slot order:** `x -> color -> facet_col -> facet_row -> animation_frame`

In [21]:
# Distribution by latitude (time aggregated into box stats)
transect = air.sel(lon=250)

transect.plotly.box(x="lat", title="Temperature Distribution by Latitude")

In [22]:
# Box plot with color grouping: lat -> x, lon -> color
multi_loc = air.sel(lat=[60, 45, 30], lon=[220, 250, 280])

multi_loc.plotly.box(
    x="lat", color="lon",
    title="Temperature Distribution by Latitude and Longitude"
)

In [23]:
# Faceted box plots: distribute dimensions across slots
subset = air.sel(lat=[60, 45, 30], lon=[220, 280]).isel(time=slice(0, 365))

subset.plotly.box(
    x="lat", color="lon",
    title="Box Plots with Color Grouping",
    height=400
)

In [24]:
# Compare: same data without color grouping (lon aggregated)
subset.plotly.box(
    x="lat",
    title="Box Plots without Lon Grouping (lon values aggregated)",
    height=400
)

---
## Heatmaps with imshow

For `imshow`, both x and y are dimensions (not values).

**Slot order:** `y (rows) -> x (columns) -> facet_col -> animation_frame`

In [25]:
# Single time snapshot
snapshot = air.isel(time=0)

# Automatic: lat -> y (rows), lon -> x (columns)
snapshot.plotly.imshow(
    title="Air Temperature Snapshot",
    color_continuous_scale="RdBu_r"
)

In [26]:
# Explicit axis assignment
snapshot.plotly.imshow(
    x="lon", y="lat",
    title="Explicit: lon on x, lat on y",
    color_continuous_scale="RdBu_r"
)

### Hovmoller Diagrams (Time-Space)

In [27]:
# Latitude vs time at one longitude
hovmoller = air.sel(lon=250).resample(time="D").mean()

hovmoller.plotly.imshow(
    x="time", y="lat",
    title="Hovmoller Diagram: Latitude vs Time",
    color_continuous_scale="RdBu_r"
)

In [28]:
# Longitude vs time at one latitude
hovmoller_lon = air.sel(lat=45).resample(time="D").mean()

hovmoller_lon.plotly.imshow(
    x="time", y="lon",
    title="Hovmoller Diagram: Longitude vs Time",
    color_continuous_scale="RdBu_r"
)

### Faceted Heatmaps

In [29]:
# Seasonal mean maps
seasonal_maps = air.groupby("time.season").mean()

seasonal_maps.plotly.imshow(
    x="lon", y="lat", facet_col="season",
    title="Seasonal Mean Temperature",
    color_continuous_scale="RdBu_r",
    facet_col_wrap=2,
    height=600
)

In [30]:
# Monthly progression
monthly_maps = air.resample(time="ME").mean().isel(time=slice(0, 6))

monthly_maps.plotly.imshow(
    x="lon", y="lat", facet_col="time",
    title="First 6 Months of 2013",
    color_continuous_scale="RdBu_r",
    facet_col_wrap=3,
    height=500
)

### Animated Heatmaps

In [31]:
# Animated daily temperature
daily_maps = air.resample(time="D").mean().isel(time=slice(0, 60))

daily_maps.plotly.imshow(
    x="lon", y="lat", animation_frame="time",
    title="Daily Temperature Animation (60 days)",
    color_continuous_scale="RdBu_r",
    zmin=-40, zmax=30
)

---
## Modifying Plots After Creation

A major advantage of Plotly over matplotlib is that all methods return a `Figure` object that can be **easily modified after creation**. No need to pass all options upfront!

### Updating Layout

In [34]:
# Create a basic plot
fig = three_lats.plotly.line()

# Modify layout after creation
fig.update_layout(
    title=dict(text="Temperature Comparison", x=0.5, font_size=20),
    xaxis_title="Date",
    yaxis_title="Temperature (°C)",
    template="plotly_white",
    legend=dict(
        title="Latitude",
        orientation="h",
        yanchor="bottom",
        y=1.02,
        xanchor="center",
        x=0.5
    ),
    hovermode="x unified"
)
fig

### Updating Traces (Lines, Markers, etc.)

In [35]:
fig = three_lats.isel(time=slice(0, 100)).plotly.line()

# Modify all traces at once
fig.update_traces(
    line=dict(width=2),
    mode="lines+markers",
    marker=dict(size=4)
)

fig.update_layout(title="Lines with Markers")
fig

In [36]:
fig = three_lats.isel(time=slice(0, 50)).plotly.line()

# Update specific traces by selector
fig.update_traces(line=dict(width=4, dash="dash"), selector=dict(name="60.0"))
fig.update_traces(line=dict(width=2), selector=dict(name="45.0"))
fig.update_traces(line=dict(width=1, dash="dot"), selector=dict(name="30.0"))

fig.update_layout(title="Different Styles per Trace")
fig

### Adding Annotations and Shapes

In [37]:
fig = air.sel(lon=250, lat=45).plotly.line()

# Add a horizontal line for the mean
mean_temp = float(air.sel(lon=250, lat=45).mean())
fig.add_hline(
    y=mean_temp,
    line_dash="dash",
    line_color="red",
    annotation_text=f"Mean: {mean_temp:.1f}°C",
    annotation_position="right"
)

# Add a shaded region
fig.add_vrect(
    x0="2013-06-01", x1="2013-08-31",
    fillcolor="orange", opacity=0.2,
    line_width=0,
    annotation_text="Summer",
    annotation_position="top left"
)

fig.update_layout(title="Time Series with Annotations")
fig

### Adding New Traces to Existing Plots

In [38]:
import plotly.graph_objects as go

# Start with a line plot
fig = air.sel(lon=250, lat=45).resample(time="ME").mean().plotly.line()

# Add min/max as a shaded range
monthly = air.sel(lon=250, lat=45).resample(time="ME")
times = monthly.mean().time.values
y_max = monthly.max().values
y_min = monthly.min().values

fig.add_trace(go.Scatter(
    x=list(times) + list(times)[::-1],
    y=list(y_max) + list(y_min)[::-1],
    fill="toself",
    fillcolor="rgba(99, 110, 250, 0.2)",
    line=dict(color="rgba(255,255,255,0)"),
    name="Min-Max Range",
    showlegend=True
))

# Move the original trace to front
fig.data = fig.data[::-1]

fig.update_layout(title="Monthly Mean with Min-Max Range")
fig

### Combining Multiple Plots with Subplots

In [39]:
from plotly.subplots import make_subplots

# Create subplot grid
fig = make_subplots(
    rows=2, cols=2,
    subplot_titles=("Line Plot", "Bar Chart", "Box Plot", "Heatmap"),
    specs=[[{}, {}], [{}, {"type": "heatmap"}]]
)

# Get data from xarray plots and add to subplots
line_fig = air.sel(lon=250, lat=45).isel(time=slice(0, 100)).plotly.line()
for trace in line_fig.data:
    fig.add_trace(trace, row=1, col=1)

bar_fig = seasonal.plotly.bar()
for trace in bar_fig.data:
    fig.add_trace(trace, row=1, col=2)

box_fig = air.sel(lon=250, lat=[60, 45, 30]).plotly.box(x="lat")
for trace in box_fig.data:
    fig.add_trace(trace, row=2, col=1)

# Add heatmap
snapshot = air.isel(time=0)
fig.add_trace(
    go.Heatmap(z=snapshot.values, x=snapshot.lon.values, y=snapshot.lat.values,
               colorscale="RdBu_r", showscale=False),
    row=2, col=2
)

fig.update_layout(height=600, showlegend=False, title_text="Combined Dashboard")
fig

### Method Chaining

In [40]:
# All update methods return the figure, enabling chaining
(
    three_lats.isel(time=slice(0, 200))
    .plotly.line()
    .update_layout(
        title="Chained Modifications",
        template="plotly_dark"
    )
    .update_traces(line_width=2)
    .update_xaxes(title="Date", showgrid=True, gridcolor="gray")
    .update_yaxes(title="Temp (°C)", showgrid=True, gridcolor="gray")
)

### Customizing Interactivity

In [41]:
fig = snapshot.plotly.imshow(color_continuous_scale="RdBu_r")

# Customize hover template
fig.update_traces(
    hovertemplate="Lon: %{x}<br>Lat: %{y}<br>Temp: %{z:.1f}°C<extra></extra>"
)

# Add buttons for interactivity
fig.update_layout(
    title="Interactive Heatmap",
    updatemenus=[
        dict(
            type="buttons",
            direction="left",
            x=0.5, y=1.15,
            xanchor="center",
            buttons=[
                dict(label="RdBu", method="update",
                     args=[{"colorscale": [[0, "blue"], [0.5, "white"], [1, "red"]]}]),
                dict(label="Viridis", method="update",
                     args=[{"colorscale": "Viridis"}]),
                dict(label="Plasma", method="update",
                     args=[{"colorscale": "Plasma"}]),
            ]
        )
    ]
)
fig

---
## Dimension-to-Slot Assignment Reference

| Method | Slot Order | Notes |
|--------|------------|-------|
| `line` | x -> color -> line_dash -> symbol -> facet_col -> facet_row -> animation_frame | y = values |
| `bar` | x -> color -> pattern_shape -> facet_col -> facet_row -> animation_frame | y = values |
| `area` | x -> color -> pattern_shape -> facet_col -> facet_row -> animation_frame | y = values |
| `scatter` | x -> color -> size -> symbol -> facet_col -> facet_row -> animation_frame | y = values (or dimension) |
| `box` | x (only) | Other slots default to None (aggregation) |
| `imshow` | y (rows) -> x (cols) -> facet_col -> animation_frame | Both x and y are dimensions |

### Assignment Rules

1. **Automatic:** Dimensions fill slots in order
2. **Explicit:** `x="dim_name"` locks a dimension to a slot
3. **Skip:** `color=None` skips that slot entirely
4. **Error:** Unassigned dimensions raise an error (except for `box` which aggregates them)